# Loading Packages

In [1]:
import os
os.environ['HF_HOME'] = '/data2/ketan/orc/HF_Cache'
import torch
import torch.nn as nn
import torch.optim as optim
from torch.utils.data import DataLoader
from surya.input.processing import prepare_image_detection
from surya.model.detection.segformer import load_processor , load_model
from datasets import load_dataset
from tqdm import tqdm
from torch.utils.tensorboard import SummaryWriter
import torch.nn.functional as F
import numpy as np 
from surya.layout import parallel_get_regions
import torch.nn.functional as F

# Initializing The Dataset And Model

In [2]:
device = torch.device("cuda:3" if torch.cuda.is_available() else "cpu")
dataset = load_dataset("vikp/publaynet_bench", split="train[:100]") # You can choose you own dataset

In [3]:
model = load_model("vikp/surya_layout2").to(device)
model.to(torch.float32)
"."

Loaded detection model vikp/surya_layout2 on device cuda with dtype torch.float16


'.'

# Helper Functions, Loss Function And Optimizer

In [4]:
optimizer = optim.Adam(model.parameters(), lr=1e-4)
log_dir = "logs"
checkpoint_dir = "checkpoints"
os.makedirs(log_dir, exist_ok=True)
os.makedirs(checkpoint_dir, exist_ok=True)
writer = SummaryWriter(log_dir=log_dir)

In [5]:
def logits_to_mask(logits, labels, bboxes, original_size=(1200, 1200)):
    batch_size, num_classes, height, width = logits.shape
    mask = torch.zeros((batch_size, num_classes, height, width), dtype=torch.float32).to(logits.device)

    for bbox, class_id in zip(bboxes, labels):
        x_min, y_min, x_max, y_max = bbox

        x_min = int(x_min * width / original_size[0])
        y_min = int(y_min * height / original_size[1])
        x_max = int(x_max * width / original_size[0])
        y_max = int(y_max * height / original_size[1])

        x_min = max(0, min(x_min, width - 1))
        y_min = max(0, min(y_min, height - 1))
        x_max = max(0, min(x_max, width - 1))
        y_max = max(0, min(y_max, height - 1))

        if x_min < x_max and y_min < y_max:
            mask[:, class_id, y_min:y_max, x_min:x_max] = torch.maximum(
                mask[:, class_id, y_min:y_max, x_min:x_max], torch.tensor(1.0).to(logits.device)
            )
        else:
            print(f"Invalid bounding box after adjustment: {bbox}, adjusted to: {(x_min, y_min, x_max, y_max)}")

    return mask


def loss_function(logits, mask):
    loss_fn = torch.nn.CrossEntropyLoss()  
    loss = loss_fn(logits, mask)
    return loss

# Fine-Tuning Process

In [6]:
num_epochs = 5

for param in model.parameters():
    param.requires_grad = True


model.train()
with torch.autograd.set_detect_anomaly(True):

    for epoch in range(num_epochs):
        running_loss = 0.0
        avg_loss = 0.0

        for idx, item in enumerate(tqdm(dataset, desc=f"Epoch {epoch + 1}/{num_epochs}")):
            images = [prepare_image_detection(img=item['image'], processor=load_processor())]
            images = torch.stack(images, dim=0).to(model.dtype).to(model.device)
            
            optimizer.zero_grad()
            outputs = model(pixel_values=images)


            logits = outputs.logits

            bboxes = item['bboxes']
            labels = item['category_ids']
            mask = logits_to_mask(logits, labels, bboxes)

            logits = logits.to(torch.float32)
            mask = mask.to(torch.float32)
            loss = loss_function(logits, mask)

            loss.backward()

            optimizer.step()

            avg_loss = 0.9 * avg_loss + 0.1 * loss.item() if idx > 0 else loss.item()

        writer.add_scalar('Training Loss', avg_loss, epoch + 1)
        print(f"Average Loss for Epoch {epoch + 1}: {avg_loss:.4f}")

        torch.save(model.state_dict(), os.path.join(checkpoint_dir, f"model_epoch_{epoch + 1}.pth"))


Epoch 1/5: 100%|██████████| 100/100 [01:46<00:00,  1.07s/it]


Average Loss for Epoch 1: 0.3322


Epoch 2/5: 100%|██████████| 100/100 [01:51<00:00,  1.11s/it]


Average Loss for Epoch 2: 0.3311


Epoch 3/5: 100%|██████████| 100/100 [01:51<00:00,  1.12s/it]


Average Loss for Epoch 3: 0.3197


Epoch 4/5: 100%|██████████| 100/100 [01:42<00:00,  1.03s/it]


Average Loss for Epoch 4: 0.3106


Epoch 5/5: 100%|██████████| 100/100 [01:46<00:00,  1.06s/it]


Average Loss for Epoch 5: 0.3160


# Loading The Checkpoint 

In [7]:
checkpoint_path = '/data2/ketan/orc/surya-layout-fine-tune/checkpoints/model_epoch_5.pth'  
state_dict = torch.load(checkpoint_path,weights_only=True)

model.load_state_dict(state_dict)

<All keys matched successfully>

In [8]:
model.to('cpu')
model.save_pretrained("fine-tuned-surya-model-layout")